## connect to google drive (working on colab)

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!mkdir moj7


In [ ]:
%cd drive

/content/drive


In [ ]:
%cd MyDrive

/content/drive/MyDrive


In [ ]:
%cd moj7

/content/drive/MyDrive/moj7


In [ ]:
!pwd

/content/drive/MyDrive/moj7


## Preprocess

In [ ]:
import re

In [ ]:
train_file ='train/in.tsv.xz'
test_file = 'test-A/in.tsv.xz'
out_file = 'test-A/out.tsv'

def preprocess(line):
    line = replace_endline(line)
    line = get_rid_of_header(line)
    return line

def get_rid_of_header(line):
    line = line.split('\t')[6:]
    return "".join(line)
    
def replace_endline(line):
    line = re.sub("\\n|\\+", " ", line)
    return line

In [ ]:
from itertools import islice
import regex as re
import sys
from torchtext.vocab import build_vocab_from_iterator
import lzma
import pickle



def get_words_from_line(line):
    line = line.rstrip()
    yield '<s>'
    line = preprocess(line)
    for t in line.split(' '):
        yield t
    yield '</s>'


def get_word_lines_from_file(file_name):
    n = 0
    with lzma.open(file_name, 'r') as fh:
        for line in fh:
            n+=1
            if n%1000==0:
                print(n)
            yield get_words_from_line(line.decode('utf-8'))
#vocab_size = 20000
vocab_size = 20000

vocab = build_vocab_from_iterator(
    get_word_lines_from_file(train_file),
    max_tokens = vocab_size,
    specials = ['<unk>'])



1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000
15

In [ ]:
vocab['no']

50

In [ ]:
with open('filename.pickle', 'wb') as handle:
    pickle.dump(vocab, handle, protocol=pickle.HIGHEST_PROTOCOL)

## Create NN

In [ ]:
from torch import nn
import torch
import pickle
# embed_size = 150
embed_size = 150

class Bigram(nn.Module):
  def __init__(self, vocabulary_size, embedding_size):
      super(Bigram, self).__init__()
      self.model = nn.Sequential(
          nn.Embedding(vocabulary_size, embedding_size),
          nn.Linear(embedding_size, vocabulary_size),
          nn.Softmax()
      )
  def forward(self, x):
      return self.model(x)

model = Bigram(vocab_size, embed_size)

vocab.set_default_index(vocab['<unk>'])
res = torch.tensor(vocab.forward(['order']))
print(res)


tensor([215])


In [ ]:
from torch.utils.data import IterableDataset
import itertools

def look_ahead_iterator(gen):
    prev = None
    for item in gen:
        if prev is not None:
            yield (prev, item)
        prev = item

class Bigrams(IterableDataset):
  def __init__(self, text_file, vocabulary_size):
      self.vocab = build_vocab_from_iterator(
         get_word_lines_from_file(text_file),
         max_tokens = vocabulary_size,
         specials = ['<unk>'])
      self.vocab.set_default_index(self.vocab['<unk>'])
      self.vocabulary_size = vocabulary_size
      self.text_file = text_file

  def __iter__(self):
     return look_ahead_iterator(
         (self.vocab[t] for t in itertools.chain.from_iterable(get_word_lines_from_file(self.text_file))))


train_dataset = Bigrams(train_file, vocab_size)

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000
121000
122000
123000
124000
125000
126000
127000
128000
129000
130000
131000
132000
133000
134000
135000
136000
137000
138000
139000
140000
141000
142000
143000
144000
145000
146000
147000
148000
149000
150000
151000
152000
153000
154000
155000
156000
157000
158000
15

In [ ]:
from torch.utils.data import DataLoader

next(iter(DataLoader(train_dataset, batch_size=5)))

[tensor([  23,  191, 5791,    1,  112]),
 tensor([ 191, 5791,    1,  112,  159])]

## Train

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [ ]:

model = Bigram(vocab_size, embed_size).to(device)
data = DataLoader(train_dataset, batch_size=1000)
optimizer = torch.optim.Adam(model.parameters())
criterion = torch.nn.NLLLoss()
## epochs=2
for i in range(2):
    print('epoch: =', i)
    model.train()
    step = 0
    for x, y in data:
       x = x.to(device)
       y = y.to(device)
       optimizer.zero_grad()
       ypredicted = model(x)
       loss = criterion(torch.log(ypredicted), y)
       if step % 100 == 0:
          print(step, loss)
       step += 1
       loss.backward()
       optimizer.step()
    torch.save(model.state_dict(), 'model.bin')    


epoch: = 0


/usr/local/lib/python3.10/dist-packages/torch/nn/modules/container.py:217: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


0 tensor(10.3037, device='cuda:0', grad_fn=<NllLossBackward0>)
100 tensor(8.7506, device='cuda:0', grad_fn=<NllLossBackward0>)
200 tensor(7.8141, device='cuda:0', grad_fn=<NllLossBackward0>)
1000
300 tensor(7.4218, device='cuda:0', grad_fn=<NllLossBackward0>)
400 tensor(7.1627, device='cuda:0', grad_fn=<NllLossBackward0>)
500 tensor(6.7964, device='cuda:0', grad_fn=<NllLossBackward0>)
2000
600 tensor(6.4704, device='cuda:0', grad_fn=<NllLossBackward0>)
700 tensor(6.3798, device='cuda:0', grad_fn=<NllLossBackward0>)
800 tensor(6.2849, device='cuda:0', grad_fn=<NllLossBackward0>)
3000
900 tensor(6.3975, device='cuda:0', grad_fn=<NllLossBackward0>)
1000 tensor(6.0096, device='cuda:0', grad_fn=<NllLossBackward0>)
1100 tensor(5.7434, device='cuda:0', grad_fn=<NllLossBackward0>)
4000
1200 tensor(5.9602, device='cuda:0', grad_fn=<NllLossBackward0>)
1300 tensor(6.1623, device='cuda:0', grad_fn=<NllLossBackward0>)
1400 tensor(6.1647, device='cuda:0', grad_fn=<NllLossBackward0>)
5000
1500 tensor

## Eval

In [ ]:

model = Bigram(vocab_size, embed_size).to(device)
model.load_state_dict(torch.load('model.bin'))
model.eval()

res = torch.tensor(vocab.forward(['for'])).to(device)

out = model(res)
top = torch.topk(out[0], 10)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

/usr/local/lib/python3.10/dist-packages/torch/nn/modules/container.py:217: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  input = module(input)


[('<unk>', 0, 0.23156249523162842),
 ('the', 1, 0.2045561522245407),
 ('a', 5, 0.0636623203754425),
 ('his', 20, 0.012841351330280304),
 ('their', 40, 0.012044394388794899),
 ('this', 28, 0.011758995242416859),
 ('tho', 33, 0.010536346584558487),
 ('some', 77, 0.008259670808911324),
 ('any', 49, 0.007337945979088545),
 ('an', 38, 0.007214350625872612)]

In [ ]:
vocab = train_dataset.vocab
res = torch.tensor(vocab.forward(['wait'])).to(device)

out = model(res)
top = torch.topk(out[0], 20)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('until', 145, 0.17603398859500885),
 ('for', 9, 0.16400693356990814),
 ('<unk>', 0, 0.15191353857517242),
 ('on', 15, 0.04624223709106445),
 ('till', 677, 0.035729214549064636),
 ('a', 5, 0.03367603197693825),
 ('to', 4, 0.029361305758357048),
 ('upon', 59, 0.01995147578418255),
 ('and', 3, 0.01906605064868927),
 ('in', 6, 0.013167516328394413),
 ('at', 14, 0.011669990606606007),
 ('the', 1, 0.010971800424158573),
 ('of', 2, 0.005925077944993973),
 ('with', 16, 0.0055325529538095),
 ('In', 32, 0.004919056314975023),
 ('until\\nthe', 5509, 0.004719363059848547),
 ('tor', 532, 0.004647853318601847),
 ('for\\nthe', 389, 0.004400868900120258),
 ('two', 74, 0.0043497709557414055),
 ('patiently', 14401, 0.004239553119987249)]

In [ ]:
cos = nn.CosineSimilarity(dim=1, eps=1e-6)

embeddings = model.model[0].weight

vec = embeddings[vocab['take']]

similarities = cos(vec, embeddings)

top = torch.topk(similarities, 10)

top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('take', 152, 1.0000001192092896),
 ('took', 248, 0.8024641275405884),
 ('taking', 538, 0.775847852230072),
 ('takes', 1108, 0.7307196855545044),
 ('to\\ntake', 3165, 0.7301462888717651),
 ('taken', 180, 0.6280043125152588),
 ('will\\ntake', 11101, 0.6152595281600952),
 ('tako', 6281, 0.5979241132736206),
 ('have\\ntaken', 15483, 0.5244049429893494),
 ('Take', 5203, 0.5183135867118835)]

In [ ]:
vocab = train_dataset.vocab
res = torch.tensor(vocab.forward(['take'])).to(device)

out = model(res)
top = torch.topk(out[0], 20)
top_indices = top.indices.tolist()
top_probs = top.values.tolist()
top_words = vocab.lookup_tokens(top_indices)
list(zip(top_words, top_indices, top_probs))

[('<unk>', 0, 0.18006379902362823),
 ('the', 1, 0.11970410495996475),
 ('a', 5, 0.07213426381349564),
 ('care', 611, 0.027887443080544472),
 ('up', 69, 0.027840441092848778),
 ('it', 17, 0.023985734209418297),
 ('place', 159, 0.020694952458143234),
 ('advantage', 1458, 0.015635941177606583),
 ('his', 20, 0.014868981204926968),
 ('part', 131, 0.013506578281521797),
 ('an', 38, 0.013118326663970947),
 ('their', 40, 0.010849231854081154),
 ('hold', 478, 0.010717789642512798),
 ('them', 72, 0.010186631232500076),
 ('to', 4, 0.009746687486767769),
 ('this', 28, 0.009519988670945168),
 ('any', 49, 0.009436620399355888),
 ('her', 53, 0.008774512447416782),
 ('him', 70, 0.008407332003116608),
 ('all', 34, 0.007673078216612339)]

### Create files for geval

In [ ]:
def get_values(presc_word, model, vocab):
    ixs =  torch.tensor(vocab.forward([presc_word])).to(device)
    out = model(ixs)
    top = torch.topk(out[0], 20)
    top_indices = top.indices.tolist()
    top_probs = top.values.tolist()
    top_words = vocab.lookup_tokens(top_indices)
    return list(zip(top_words, top_probs))

def last_word(text):
    """Return the last word of a string."""
    last_word = ""
    for i in range(len(text)-1, -1, -1):
        if text[i] == ' ':
            return last_word[::-1]
        else:
            last_word += text[i]
    return last_word[::-1]

def first_word(text):
    """Return the first word of a string."""
    word = ""
    for i in range(len(text)-1):
        if text[i] == ' ':
            return word
        else:
            word += text[i]
    return word

def sum_prob(dic):
    probsum = sum(float(val) for key, val in dic.items())
    probsum = probsum - float(dic.get('<unk>', 0))
    if "<unk>" in dic.keys():
        del dic['<unk>']
    tab = [(key, val) for key, val in dic.items()]
    tab.append(('<unk>', 1-probsum))
    return tab

def format_to(dic):
    tab = sum_prob(dic)
    result = ''
    for element in tab[:-1]:
        result+=str(element[0])+':'+str(element[1])+'\t'
    result+=':'+ str(tab[-1][1])+'\n'
    return result

In [ ]:
with lzma.open(test_file, 'rt') as file:
    predict_words = []
    results = []
    for line in file:
        split = line.split('\t')[6:] 
        predict_words.append(last_word(split[0]))
    
    vocab = train_dataset.vocab
    for presc_word in predict_words:
        results.append(dict(get_values(presc_word, model ,vocab)))
    
    with open(out_file, 'w') as outfile:
        for elem in results:
            outfile.write(format_to(elem))

